# Лабораторная работа №2

## Постановка задачи

Реализовать стандартное нормальное распределение случайной величиный:
- Как сумму равномерно распределенных в отрезке $[0, 1]$ случайных величин (ЦПТ);
- С использованием метода Бокса-Мюллера;
- С использованием алгоритма Метрополиса

In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

from plotly.subplots import make_subplots

Функция для построения гистограммы.

## Реализации стандартного нормального распределения случайной величины

### Центрально предельная теорема (ЦПТ)

#### Описание

Пусть нам необходимо получить ряд случайных чисел $x$, распределенных по нормальному закону с заданными математическим ожиданием $\mu_x$ и среднеквадратичным отклонением $\sigma_x$.

Сложим $n$ случайных чисел равномерно распределенных на интервале $[0, 1]$, используя стандартный *генератор случайных чисел*:
$$ S = \sum_{i=1}^{n} \xi_i.$$

Согласно ЦПТ числа $S$ образуют ряд значений, распределенный по нормальному закону. На практике $n$ берут равными $6$ или $12$. Закон распределения чисел $S$ имеет математическое ожидание 
$$\mu_S = \dfrac{n}{2},~~~\sigma_S = \sqrt{\dfrac{n}{12}}.$$

Поэтому он является смещенным относительно заданного произвольного.


С помощью формулы 
$$z = \dfrac{S – \mu_S}{\sigma_S}$$ 

нормализуем этот ряд. Получим нормализованный закон нормального распределения чисел $z$. То есть $\mu_z = 0$, $\sigma_z = 1$.

Формулой (сдвиг на $\mu_x$ и масштабирование на $\sigma_x$) преобразуем ряд $z$ в ряд $x$: $x = z · \sigma_x + \mu_x$.

#### Реализация

In [2]:
def central_limit_theorem(mean, std):
    np.random.seed()
    n = 12 # Число случайных чисел
    
    z = (np.sum(1. * np.random.sample(n)) - 0.5 * n) / np.sqrt(n / 12.)
    return z * std + mean

### Метод Бокса-Мюллера

Пусть $\eta$ и $\xi~-$ независимые случайные величины, равномерно распределенные на интервале $[0, 1]$. Тогда величины $x$ и $y$:

$$x = \cos(2\pi\xi)\sqrt{-2  \ln(1 - \eta)},$$

$$y = \sin(2\pi\xi)\sqrt{-2  \ln(1 - \eta)} $$

будут независимы и распределенны нормально с математическим ожиданием $0$ и дисперсией $1$.
Аналогично ЦПТ, преобразуем полученны случайные величины для заданных математического ожидания и среднеквадратичного отклонения.

#### Реализация

In [3]:
def box_muller_method(mean, std):
    np.random.seed()
    
    eta = np.random.uniform()
    xi = np.random.uniform()
    
    return (
        np.sqrt(-2 * np.log(1 - eta)) * np.cos(2 * np.pi * xi) * std + mean,
        np.sqrt(-2 * np.log(1 - eta)) * np.sin(2 * np.pi * xi) * std + mean
    )

### Алгоритм Метрополиса

#### Описание
Метод генерации многомерной случайной величины с заданной плотностью вероятности $\omega(x)$, основанный на случайном блуждании в $x$ пространстве. Чем дольше длится блуждание, тем точнее последовательность точек апроксимирует $\omega(x)$.

1) Задается пробный шаг $x_t = x_n + \delta$, где $\delta = \delta(\eta_1, \eta_2, ..., \eta_d),~~~\eta_i \in [-1, 1]$;

2) Вычисляется 
$$r=\frac{\omega(x_t)}{\omega(x_n)}.$$

В нашем случае $\omega(x) = \dfrac{1}{\sqrt{2\pi}} \exp\Bigl[{\dfrac{-x^2}{2}}\Bigr]$.

- Если $r \geq 1$, то $x_{n + 1} = x_t$, в противном случае генерируем $\xi \in [0, 1]$,
- Если $r > \xi$, то $x_{n + 1} = x_t$, в противном случае $x_{n + 1} = x_n.$

3) Повтор предыдущих пунктов.

#### Реализация

In [4]:
def omega(x, mu, sigma):
    return np.exp(-0.5 * (x - mu)**2 / (sigma**2)) / (sigma * np.sqrt(2 * np.pi))


def metropolis(mean, std, dimension, step, total):
    np.random.seed()
    
    x_n = np.zeros(dimension)

    for _ in range(total):
        delta = (1. - (-1)) * np.random.sample(dimension) - 1
        x_t = x_n + step * delta

        r = omega(x_t, mean, std) / omega(x_n, mean, std)
        
        for i in range(len(r)):
            if r[i] >= 1:
                x_n[i] = x_t[i]
        
            else:
                xi = np.random.uniform()
                x_n[i] = x_t[i] if r[i] > xi else x_n[i]

    return x_n

Визуализируем изменения результатов моделирования (объем выборки $N = 500$) нормального распределения ($\mu = 4$, $\sigma = 1$) при увеличении количества термализационных шагов (размер шага $1$).

In [5]:
def data(mu, sigma, values_step, count_steps, parametrs):
    
    metropolis_array = np.array([])
    steps = np.array([], dtype=int)
    
    if parametrs == 'count steps':
        for item in count_steps:
            metropolis_array = np.append(
                metropolis_array, 
                metropolis(mu, sigma, 500, values_step, item)) 
            steps = np.append(steps, np.full((500, ), item, dtype=int))
                
    elif parametrs == 'values step':
        for item in values_step:
            metropolis_array = np.append(
                metropolis_array, 
                metropolis(mu, sigma, 500, item, count_steps))
            steps = np.append(steps, np.full((500, ), item))
            
    else:
        raise Exception
        
    x = np.linspace(mu - 4, mu + 4, 200)
    
    df_hist  = pd.DataFrame({'random variable value': metropolis_array, parametrs: steps})
    df_omega = pd.DataFrame({'x': x, 'omega': omega(x, mu, sigma)})
    
    return df_hist, df_omega

In [6]:
def plotly_histogram(df, omega, animation_frame, mu, sigma, title):
    fig = px.histogram(df, animation_frame=animation_frame,
                   color_discrete_sequence=['rgb(0, 0, 100)'], opacity=0.7, histnorm='probability density',
                  title=title)

    fig.add_scatter(x=omega['x'], y=omega['omega'], 
                marker=dict(color='rgb(0, 200, 200)', size=3.2,), mode='markers', 
                    name=r'$\mu = {},~~\sigma = {}$'.format(mu, sigma))

    fig.show()

In [7]:
# Набор значений количества шагов
count_steps = range(1, 100, 2)

# Данные для визуализации
df_hist, df_omega = data(4, 1, 1, count_steps, 'count steps')

In [8]:
plotly_histogram(df_hist, df_omega, 'count steps', 4, 1,
                'Normal distribution with different number of thermalization steps in the Metropolis Algorithm')

Рассмотрим зависимость мат ожидания $\mu$ и среднеквадратичного отклонения $\sigma$ случайной величины от числа термализационных шагов.

In [32]:
def mean_plot(df, group):
    df = df.groupby(group, as_index=False).mean()

    fig.add_trace(go.Scatter(x=df[group], y=df['random variable value'], mode="lines+markers"), 
                  row=1, col=1)
    fig.update_yaxes(title_text=r'$\text{expected value }(\mu)$', col=1)
    fig.update_xaxes(title_text=r'$\text{count steps}$')
    
    
def std_plot(df, group):
    df = df.groupby(group, as_index=False).std()

    fig.add_trace(go.Scatter(x=df[group], y=df['random variable value'], mode="lines+markers"), row=1, col=2)

    fig.update_yaxes(title_text=r'$\text{standard deviation }(\sigma)$', col=2)
    fig.update_xaxes(title_text=f'{group}')
   

In [33]:
fig = make_subplots(rows=1, cols=2, 
                    subplot_titles=(r'$\text{Dependence of }\mu\text{ on the number of thermalization steps}$', 
                                    r'$\text{Dependence of }\sigma\text{ on the number of thermalization steps}$'))
                    
mean_plot(df_hist, 'count steps')
std_plot(df_hist, 'count steps')

fig.update_layout(showlegend=False)
fig.show()

Из графиков видно, что мат ожидание и среднеквадратичное отклонения при увеличении числа термализационных шагов сходятся к заранее заданым значениям. Таким образом распределение моделируемой выборки приближается к нормальному распределению.

Визуализируем изменения нормального распределения при увеличении размера шага.

In [12]:
df_hist_, df_omega_ = data(4, 1, np.around(np.arange(0.0, 1.550, 0.05), decimals=3), 25, 'values step')

In [13]:
plotly_histogram(df_hist_, df_omega_, 'values step', 4, 1,
                'Normal distribution with different values step in the Metropolis Algorithm')

Рассмотрим зависимость мат ожидания $\mu$ и среднеквадратичного отклонения $\sigma$ случайной величины от размера термализационного шага.

In [29]:
fig = make_subplots(rows=1, cols=2, 
                    subplot_titles=(r'$\text{Dependence of }\mu\text{ on the value of the thermalization step}$', 
                                    r'$\text{Dependence of }\sigma\text{ on the value of the thermalization step}$'))

mean_plot(df_hist_, 'values step')
std_plot(df_hist_, 'values step')

fig.update_layout(showlegend=False)
fig.show()

### Сравнение методов

#### Гистограмма распределения

Создадим dataframe содержащий $1000$ значений случайной величины для каждой реализации.

In [15]:
a = np.array([])
df = pd.DataFrame({
    'central limit theorem' : [central_limit_theorem(-4, 1) for _ in range(500)],
    'box muller method':   (np.append(a, [box_muller_method(0, 1) for _ in range(250)])),
    'metropolis': metropolis(4, 1, 500, 1, 50),
})

Для удобства визуализации, каждый полученный набор случайных величин был расчитан при разном мат ожидании
- центральная предельная теорема: $\mu = -4$,
- метод Бокса-Мюллера: $\mu = 0$,
- алгоритм Метрополиса: $\mu = 4$.

Для каждого случая $\sigma = 1$.

In [16]:
fig = px.histogram(df, histnorm='probability density', nbins=100, title='Distribution histograms')

fig.add_scatter(x=np.linspace(-4., 4., 300), y= omega(np.linspace(-4., 4., 300), 0, 1), 
                marker=dict(size=3.2), mode='markers', name=r'$\mu = 0$')

fig.add_scatter(x=np.linspace(-8., 0, 300), y= omega(np.linspace(-8., 0, 300), -4, 1), 
                marker=dict(size=3.2), mode='markers', name=r'$\mu = -4$')

fig.add_scatter(x=np.linspace(0., 8., 300), y= omega(np.linspace(0., 8., 300), 4, 1), 
                marker=dict(size=3.2), mode='markers', name=r'$\mu = 4$')

fig.update_layout(barmode='overlay')
fig.update_traces(opacity=0.75)

fig.show()

#### Среднее значение и дисперсия

Построим зависмость значения среднего от объема выборки.

In [17]:
def avg(array):
    return np.mean(array)

def dispersion(array):
    return avg(array**2) - avg(array)**2

In [18]:
#print(np.logspace(1.5, 4.4, 40, dtype=int))

In [19]:
def data_(mean, std, method, name):
    
    avgs = np.array([])
    dispersions = np.array([])

    totals = np.logspace(1.5, 4.4, 40, dtype=int)

    for n in totals:
        if name == 'metropolis':
            array = method(mean, std, n)
        else:
            array = np.array([method(mean, std) for _ in range(n)])
        
        avgs = np.append(avgs,  avg(array))
        dispersions = np.append(dispersions, dispersion(array))
    
    return pd.DataFrame({
        "totals": totals, 
        "average": avgs, 
        "dispersion": dispersions, 
        "method": [name] * len(totals)
    })


def box_muller(mean, std):
    return box_muller_method(mean, std)[0]

def _metropolis(mean, std, n):
    return metropolis(mean, std, n, 1, 60)

In [20]:
df_1 = data_(4, 1, central_limit_theorem,'central limit theorem')
df_2 = data_(4, 1, box_muller, 'box muller method')
df_3 = data_(4, 1, _metropolis, 'metropolis')

In [21]:
frames = [df_1, df_2, df_3]
result = pd.concat(frames)
result.groupby('method')[['average', 'dispersion']].mean()

average  dispersion
method                                     
box muller method      4.021904    1.005427
central limit theorem  3.973871    0.988032
metropolis             3.989308    1.007190

In [22]:
fig = px.line(result, x='totals', y='average', color='method', markers=True, log_x=True)
fig.show()

In [23]:
fig = px.line(result, x='totals', y='dispersion', color='method', markers=True, log_x=True)
fig.show()

#### Коэффициенты асимметрии и эксцесса

*Коэффициент асимметрии для случайной величины*
$$A_{c} = \frac{m_3}{\sigma^3}, $$

где $m_3 = \dfrac{\sum\limits_{i=1}^{n} (x_i - \mu)^3}{n}~-$ центральный теоретический момент 3-го порядка, $\mu~-$ мат ожидание, $\sigma~-$ среднее квадратичное отклонение случайной величины.

In [24]:
def asym_coef(mu, sigma, array):
    array = np.array(array)
    return np.mean((array - mu)**3) / sigma**3

In [25]:
print(asym_coef(-4, 1, df['central limit theorem']))
print(asym_coef(0, 1, df['box muller method']))
print(asym_coef(4, 1, df['metropolis']))

-0.07521471361561151
-0.2069153586040874
-0.43836855140435926


*Коэффициент эксцесса*

$$E_k = \dfrac{m_4}{\sigma^4} - 3,$$
где 
$m_4 = \dfrac{\sum\limits_{i=1}^{n} (x_i - \mu)^4}{n}~-$ центральный теоретический момент четвертого порядка.

In [26]:
def kurtosis_coef(mu, sigma, array):
    array = np.array(array)
    return (np.mean((array - mu)**4) /  sigma**4) - 3

In [27]:
print(kurtosis_coef(-4, 1, df['central limit theorem']))
print(kurtosis_coef(0, 1, df['box muller method']))
print(kurtosis_coef(4, 1, df['metropolis']))

-0.005296557993663242
0.307765505517692
0.2331717763195602
